In [21]:
import pretty_midi
import mido
import numpy as np
from pydub import AudioSegment
from IPython.display import Audio
from tempfile import NamedTemporaryFile
import os
import librosa
import soundfile as sf

In [22]:
def note_name(n):
    """Convert MIDI note number to name, e.g., 60 -> C4"""
    return pretty_midi.note_number_to_name(n)

def create_midi_from_notes(note_sequence, output_path="output.mid", instrument_name="Acoustic Grand Piano", tempo=120):
    midi = pretty_midi.PrettyMIDI(initial_tempo=tempo)
    instrument = pretty_midi.Instrument(program=pretty_midi.instrument_name_to_program(instrument_name))

    start = 0.0

    for item in note_sequence:
        # Handle flexible formats
        if isinstance(item, str):
            note_name, duration, velocity = item, 0.5, 100
        elif len(item) == 2:
            note_name, duration = item
            velocity = 100
        elif len(item) == 3:
            note_name, duration, velocity = item
        else:
            raise ValueError("Each note must be a string, (note, duration), or (note, duration, velocity)")

        if note_name == "rest":
            start += duration
            continue

        note_number = pretty_midi.note_name_to_number(note_name)
        note = pretty_midi.Note(
            velocity=velocity,
            pitch=note_number,
            start=start,
            end=start + duration
        )
        instrument.notes.append(note)
        start += duration

    midi.instruments.append(instrument)
    midi.write(output_path)
    print(f"✅ MIDI saved to {output_path}")
    return output_path


def insert_tempo_changes(midi_in_path, tempo_changes, midi_out_path):
    """
    midi_in_path: path to base MIDI file
    tempo_changes: list of (time_in_seconds, bpm), ordered by time ascending
    midi_out_path: path to save MIDI with tempo changes
    """
    mid = mido.MidiFile(midi_in_path)
    ticks_per_beat = mid.ticks_per_beat

    # Build a list of tempo change messages with correct delta ticks
    tempo_msgs = []
    last_tick = 0
    last_time = 0
    current_tempo = 500000  # default microseconds per beat (120bpm)

    for time_sec, bpm in tempo_changes:
        # Convert time_sec to ticks, accounting for previous tempo changes
        target_tick = mido.second2tick(time_sec, ticks_per_beat, current_tempo)
        delta = int(target_tick - last_tick)
        tempo_us = int(60_000_000 / bpm)
        msg = mido.MetaMessage('set_tempo', tempo=tempo_us, time=delta)
        tempo_msgs.append(msg)
        last_tick = target_tick
        current_tempo = tempo_us

    # Insert tempo change messages at start of first track
    track = mid.tracks[0]

    # Remove existing tempo messages from the track
    track = [msg for msg in track if not (msg.is_meta and msg.type == 'set_tempo')]

    # Insert our tempo messages at the start, preserving delta times
    mid.tracks[0] = tempo_msgs + track

    mid.save(midi_out_path)
    print(f"MIDI with tempo changes saved: {midi_out_path}")


fluidsynth_path = "/usr/local/bin/fluidsynth"
def midi_to_wav(midi_path, sf2_path, output_wav, fluidsynth_exe=fluidsynth_path):
    import subprocess

    try:
        subprocess.run(
            [fluidsynth_exe, "-ni", sf2_path, midi_path, "-F", output_wav, "-r", "44100"],
            check=True,
            stdout=subprocess.PIPE,
            stderr=subprocess.PIPE,
        )
        print(f"✅ Audio written to {output_wav}")
        return output_wav
    except subprocess.CalledProcessError as e:
        print("❌ FluidSynth failed:")
        print(e.stderr.decode())
        return None
    
def trim_silence(input_wav, output_wav):
   # Trim silence from the end of a WAV file using librosa.
        y, sr = librosa.load(input_wav, sr=None)
        y_trimmed, _ = librosa.effects.trim(y, top_db=20)
        sf.write(output_wav, y_trimmed, sr)
        print(f"✅ Trimmed silence and saved to {output_wav}")
        return output_wav

In [23]:
mary_notes = [
    ("E4", 0.5, 100), 
    ("D4", 0.5, 100),
    ("C4", 0.5, 100),
    ("D4", 0.5, 100),
    ("E4", 0.5, 100),
    ("E4", 0.5, 100),
    ("E4", 1.0, 100),  
    ("D4", 0.5, 100),
    ("D4", 0.5, 100),
    ("D4", 1.0, 100),
    ("E4", 0.5, 100),
    ("G4", 0.5, 100),
    ("G4", 1.0, 100)
]
mary_dynamics = [
    ("E4", 0.5, 120), ("D4", 0.5, 110), ("C4", 0.5, 100), ("D4", 0.5, 90),
    ("E4", 0.5, 80),  ("E4", 0.5, 70),  ("E4", 1.0, 60),
    ("D4", 0.5, 70),  ("D4", 0.5, 80),  ("D4", 1.0, 90),
    ("E4", 0.5, 100), ("G4", 0.5, 110), ("G4", 1.0, 120)
]
mary_extended = mary_notes + [
    ("E4", 0.5, 100), ("D4", 0.5, 100), ("C4", 0.5, 100), ("D4", 0.5, 100),
    ("E4", 0.5, 100),  ("E4", 0.5, 100),  ("E4", 0.5, 100),
    ("E4", 0.5, 100),  ("D4", 0.5, 100),  ("D4", 0.5, 100),
    ("E4", 0.5, 100), ("D4", 0.5, 100), ("C4", 1.0, 100)
]

# Tempo changes: start at 120 bpm, slow to 80 bpm at 4 seconds, speed up to 140 bpm at 8 seconds
tempo_changes_mary = [
    (4, 80),
    (8, 140),
]

twinkle_notes = [
    ("C4", 0.5, 100),
    ("C4", 0.5, 100),
    ("G4", 0.5, 100),
    ("G4", 0.5, 100),
    ("A4", 0.5, 100),
    ("A4", 0.5, 100),
    ("G4", 1.0, 100),
    ("F4", 0.5, 100),
    ("F4", 0.5, 100),
    ("E4", 0.5, 100),
    ("E4", 0.5, 100),
    ("D4", 0.5, 100),
    ("D4", 0.5, 100),
    ("C4", 1.0, 100)
]
twinkle_dynamics = [
    ("C4", 0.5, 60),  ("C4", 0.5, 70),  ("G4", 0.5, 80),  ("G4", 0.5, 90),
    ("A4", 0.5, 100), ("A4", 0.5, 110), ("G4", 1.0, 120),
    ("F4", 0.5, 120), ("F4", 0.5, 110), ("E4", 0.5, 100), ("E4", 0.5, 90),
    ("D4", 0.5, 80),  ("D4", 0.5, 70),  ("C4", 1.0, 60)
]
twinkle_extended = twinkle_notes + [
    ("G4", 0.5, 100), ("G4", 0.5, 100), ("F4", 0.5, 100), ("F4", 0.5, 100),
    ("E4", 0.5, 100), ("E4", 0.5, 100), ("D4", 1.0, 100), 
    ("G4", 0.5, 100), ("G4", 0.5, 100), ("F4", 0.5, 100), ("F4", 0.5, 100),
    ("E4", 0.5, 100), ("E4", 0.5, 100), ("D4", 1.0, 100)
]

# Tempo changes: start at 100 bpm, speed up to 160 bpm gradually over 12 seconds
tempo_changes_twinkle = [
    (0, 80),
    (2, 100),
    (4, 120),
    (6, 140),
    (8, 160),
]

In [24]:
mary_midi = create_midi_from_notes(mary_notes, "./midi/mary.mid")
twinkle_midi = create_midi_from_notes(twinkle_notes, "./midi/twinkle.mid")

mary_dynamics_midi = create_midi_from_notes(mary_dynamics, output_path="./midi/mary_dynamics.mid", tempo=120)
twinkle_dynamics_midi = create_midi_from_notes(twinkle_dynamics, output_path="./midi/twinkle_dynamics.mid", tempo=120)

mary_extended_midi = create_midi_from_notes(mary_extended, output_path="./midi/mary_extended.mid", tempo=120)
mary_tempo_midi = insert_tempo_changes("./midi/mary_extended.mid", tempo_changes_mary, "./midi/mary_tempo.mid")

twinkle_extended_midi = create_midi_from_notes(twinkle_extended, output_path="./midi/twinkle_extended.mid", tempo=100)
twinkle_tempo_midi = insert_tempo_changes("./midi/twinkle_extended.mid", tempo_changes_twinkle, "./midi/twinkle_tempo.mid")


✅ MIDI saved to ./midi/mary.mid
✅ MIDI saved to ./midi/twinkle.mid
✅ MIDI saved to ./midi/mary_dynamics.mid
✅ MIDI saved to ./midi/twinkle_dynamics.mid
✅ MIDI saved to ./midi/mary_extended.mid
MIDI with tempo changes saved: ./midi/mary_tempo.mid
✅ MIDI saved to ./midi/twinkle_extended.mid
MIDI with tempo changes saved: ./midi/twinkle_tempo.mid


In [25]:
sf2_path = "./soundfiles/FluidR3_GM.sf2"

mary_wav = midi_to_wav("./midi/mary.mid", sf2_path=sf2_path, output_wav="./wav/mary.wav")
twinkle_wav = midi_to_wav("./midi/twinkle.mid", sf2_path=sf2_path, output_wav="./wav/twinkle.wav")

mary_dynamics_wav = midi_to_wav("./midi/mary_dynamics.mid", sf2_path=sf2_path, output_wav="./wav/mary_dynamics.wav")
twinkle_dynamics_wav = midi_to_wav("./midi/twinkle_dynamics.mid", sf2_path=sf2_path, output_wav="./wav/twinkle_dynamics.wav")

mary_tempo_wav = midi_to_wav("./midi/mary_tempo.mid", sf2_path=sf2_path, output_wav="./wav/mary_tempo.wav")
twinkle_tempo_wav = midi_to_wav("./midi/twinkle_tempo.mid", sf2_path=sf2_path, output_wav="./wav/twinkle_tempo.wav")


✅ Audio written to ./wav/mary.wav
✅ Audio written to ./wav/twinkle.wav
✅ Audio written to ./wav/mary_dynamics.wav
✅ Audio written to ./wav/twinkle_dynamics.wav
✅ Audio written to ./wav/mary_tempo.wav
✅ Audio written to ./wav/twinkle_tempo.wav


In [27]:
wav_files = ["./wav/mary.wav", 
             "./wav/twinkle.wav",
             "./wav/mary_dynamics.wav",
             "./wav/twinkle_dynamics.wav", 
             "./wav/mary_tempo.wav",
             "./wav/twinkle_tempo.wav"
            ]

 # Process each file
for wav in wav_files:
   trim_silence(wav, wav)

✅ Trimmed silence and saved to ./wav/mary.wav
✅ Trimmed silence and saved to ./wav/twinkle.wav
✅ Trimmed silence and saved to ./wav/mary_dynamics.wav
✅ Trimmed silence and saved to ./wav/twinkle_dynamics.wav
✅ Trimmed silence and saved to ./wav/mary_tempo.wav
✅ Trimmed silence and saved to ./wav/twinkle_tempo.wav


In [28]:
Audio(filename="./wav/mary.wav")

In [29]:
Audio(filename="./wav/twinkle.wav")

In [30]:
Audio(filename="./wav/twinkle_dynamics.wav")

In [31]:
Audio(filename="./wav/mary_dynamics.wav")

In [32]:
Audio(filename="./wav/mary_tempo.wav")

In [34]:
Audio(filename="./wav/twinkle_tempo.wav")